In [368]:
import os
import csv
import heapq
import numpy as np

In [369]:
class Node:
    
    def __init__(self, parent = None, color= None, index = -1, degree = -1):
        
        self.color = color
        self.index = index
        self.degree = degree
        self.parent = parent
        self.child_indices = []
        self.depth = 0
        if parent:
            self.depth = parent.depth+1    
            
    def __repr__(self):
        """Use by calling repr(node)"""
        return "Node(c: " + repr(self.color) + ", idx: " + repr(self.index) + ", deg: " + repr(self.degree) + ")"    
    
    def expand(self, index):
        if index in self.child_indices:
            #print('Index already exists in the children list')
            return False
        else:
            self.child_indices.append(index)
            #print('Node %d: add child index %d' % (self.index, index))
            return True
            
    def set_color(self, color):
        self.color = color
        
    def __lt__(self, other):
        return self.degree > other.degree
    
class Graph:# undirected
    
    def __init__(self, edges=None, root=None):
        self.edges = None
        self.root = None
        self.vertices = dict()#[]# index to the list denotes the vertex index
        #self.vertex_info = []# heapq collecting index and degree
        
    def add_vertex(self, index, child):
        #print('In add_vertex, ', self.vertices ) 
        if index in self.vertices: #index < len(self.vertices):
            self.vertices[index].degree += 1
            #self.vertex_info[index].degree +=1
            #print('In add_vertex, Add degree to vertex %d' % index)
            #print('Index %d, Vertex degree %d' % (index, self.vertices[index].degree))
        else:
            parent, color, degree = None, None, 1
            self.vertices[index] = Node(parent, color, index, degree)
            #self.vertex_info.append(NodeInfo(index, degree))
            #print('Index {}, Node {}'.format(index, self.vertices[index]))
            #print('In add_vertex, Add new vertex %d' % index)
        self.vertices[index].expand(child)
        
        #print('Vertices \n', self.vertices)
        #heapq.heapify(self.vertices)
        #print('Vertex Info\n', self.vertex_info)        
            
    def set_edges(self,edges):
        self.edges = edges
        for edge in edges:
            # build a list of vertices
            self.add_vertex(edge[0], edge[1])
            self.add_vertex(edge[1], edge[0])
            
        #print('Vertices \n', self.vertices)
        #heapq.heapify(self.vertices)
        #print('Vertex Info\n', self.vertex_info)
        
    def print_graph(self):
        for index, vertex in self.vertices.items():
            rep = "Index " + str(index) + ", Node(c: " + str(vertex.color) + ", idx: " + str(vertex.index) + ", deg: " + str(vertex.degree)
            if vertex.child_indices:
                rep = rep + ", children: "+','.join([ str(child) for child in vertex.child_indices]) + ' )'
            print(rep)
                
        

In [370]:
def get_color(colors):
    
    color = None
    if not colors: color = 1
    else: color = max(colors)+1
        
    return color

def get_usable_color(index, vertices, colors):
    
    child_colors = set([vertices[cidx].color for cidx in vertices[index].child_indices if vertices[cidx].color != None])

    return colors.difference(child_colors)

def update_color_frequency(color, color_frequency):
    if color in color_frequency: color_frequency[color] += 1
    else: color_frequency[color] = 1
    print('Update frequency of color %d with frequence %d' % (color, color_frequency[color]))

In [371]:
def print_graph(vertices):
    
    for index, vertex in vertices.items():
        rep = "Index " + str(index) + ", Node(c: " + str(vertex.color) + ", idx: " + str(vertex.index) + ", deg: " + str(vertex.degree)
        if len(vertex.child_indices) > 0 and len(vertex.child_indices) < 20:
            rep = rep + ", children: "+','.join([ str(child) for child in vertex.child_indices]) + ' )'
        print(rep)

In [372]:
def node_coloring(cindex, pindex, colors, vertices):
    """
        cindex is child index and 
        pindex is parent index
        if child degree > parent degree and if 
        there is only 1 existing color usable for the child node, set that color to child node
    """
    #print('In node coloring, pindx {}, cindex{}'.format(pindex, cindex))
    color = None
    
    #print('In node coloring, vertices', vertices)
    #print('In node coloring, colors', colors)
    if vertices[cindex].color != None: 
        print('Vertex %d already have color' % cindex)
        return True, color
#     if pindex and vertices[cindex].degree < vertices[pindex].degree:
#         print('Child has less degree than parent')
#         return False, color
    

    usable_colors = get_usable_color(cindex, vertices, colors)
    #print('In node coloring, usable colors', usable_colors)
    if len(usable_colors) != 1:  
        print('More than 1 color to use')
        return False, color
    
    color = usable_colors.pop() 
    if pindex:
        print('In node_coloring, parent vertex {} with degree {}, child vertex {} with degree {} set to color {}'.\
                  format(pindex, vertices[pindex].degree, cindex, vertices[cindex].degree, color)) 
    else:
        print('In node_coloring,child vertex {} with degree {} set to color {}'.\
                  format(cindex, vertices[cindex].degree, color))        
    
    return True, color       


In [373]:
def graph_coloring_probe(index, pindex, colors, vertices):
    
    
    if pindex == None: print('In graph_coloring_probe, pindx {}, cindex {}'.format(pindex, index))
    
    #if vertices[index].color != None:
    #    print('In graph_coloring_probe, pindx {}, cindex{}'.format(pindex, index))
    #    return colors, vertices, explored
    
    flag, color = node_coloring(index, pindex, colors, vertices)
        #print('In graph_coloring_probe, node_colring returns flag {}, color {}'.format(flag, color))
    
    print('In graph_coloring_probe, index {}: node_coloring return {} with color {}'.format(index, flag, color))
    if flag:
        #print('Color {}, Color set {}'.format(color, colors))
        if color != None:
            vertices[index].color = color
            colors.add(color) 
            #update_color_frequency(color, color_frequency)
            #explored.add(index)
            print('In graph_coloring_probe, child vertex {} with degree {} set to color {}'.\
                  format(index, vertices[index].degree, color))
            #print_graph(vertices)
            
        if not vertices[index].child_indices:
            return colors, vertices            
            
        # after update, propagate the child see whether we have update more
        print('In graph_coloring_probe, check child of %d' % index)
        for cindex in vertices[index].child_indices:
            print('\nIn graph_coloring_probe, check child {} of parent {}'.format(cindex, index))
            if vertices[cindex].color != None:
                print('In graph_coloring_probe, child already set to %d' % vertices[cindex].color)
                continue
            graph_coloring_probe(cindex, index, colors, vertices)
        return colors, vertices
    else:
        print('In graph_coloring_probe, no color to set')
        return colors, vertices
    
def check_all_node(colors, vertices, explored):
    
    vertex_info =  []
    for idx, vertex in vertices.items():
        #child_colors = [vertices[cidx].color for cidx in vertex.child_indices]
        #print('In check_all_node, index {}, child colors {}'.format(vertex.index, child_colors))
        #if vertex.color and all(child_colors):
        #    print('In check_all_node, Add node %d to explored' % vertex.index)
        #    explored.add(vertex.index)
        if vertex.index not in explored:
            heapq.heappush(vertex_info, (-vertex.degree, vertex.index))        

    #print('\nIn check_all_node, vertex info ', vertex_info)
    
    while vertex_info:
        info = heapq.heappop(vertex_info)
        index = info[1]
        if index in explored: continue   
        print('\n\nIn check_all_node, check index {}'.format(index))
        colors, vertices = graph_coloring_probe(index, None, colors, vertices)  
            
    for idx, vertex in vertices.items():
        child_colors = [vertices[cidx].color for cidx in vertex.child_indices]
        #print('In check_all_node, index {}, child colors {}'.format(vertex.index, child_colors))
        if vertex.color and all(child_colors):
            print('In check_all_node, Add node %d to explored' % vertex.index)
            explored.add(vertex.index)
            
    return colors, vertices, explored
        
def graph_coloring(vertices):
    
    explored = set()
    colors = set()
    color_frequency = dict()
    
    vertex_info = []
    for idx, v in vertices.items():
        heapq.heappush(vertex_info, (-v.degree, v.index))
    
    while vertex_info:

        vinfo = heapq.heappop(vertex_info)
        #print('\n\n New vertex %d with degree %d' % (vinfo[1], -vinfo[0]))
        
        index = vinfo[1]
        if index in explored: continue
  
        color = get_color(colors)
        print('\nIn graph_coloring, Start set new color %d to index %d with degree %d' % (color,index, -vinfo[0]))
        
        # set color
        vertices[index].color = color
        colors.add(color) 
        #update_color_frequency(color, color_frequency)
        #explored.add(index)

        colors, vertices, explored = check_all_node(colors, vertices, explored)
        print('\nIn graph coloring, Finish vertex{}, add color {} color set {}'.format(index, color, colors))

        print('In graph coloring, vertices')
        print_graph(vertices)

    
    #selected_colors = [vertices[i].color for i in range(len(vertices))]
    return len(colors), [vertices[i].color-1 for i in range(len(vertices))], vertices, color_frequency



In [374]:
def solve_it(input_data):
    # Modify this code to run your optimization algorithm

    # parse the input
    lines = input_data.split('\n')

    first_line = lines[0].split()
    node_count = int(first_line[0])
    edge_count = int(first_line[1])
    #print('Node count %d, edge count %d' % (node_count, edge_count))

    edges = []
    for i in range(1, edge_count + 1):
        line = lines[i]
        parts = line.split()
        edges.append((int(parts[0]), int(parts[1])))
        
    #### play with graph
    graph = Graph()
    graph.set_edges(edges)
    #graph.print_graph()
    #print('---------------Start graph coloring ------------------')
    num_colors, solution, vertices, color_frequency = graph_coloring(graph.vertices)
    #print('Vertices ', vertices)
    vertex_colors = [(v.index, v.color) for k, v in vertices.items()]
    #print('Vertex color', [(v.index, v.color) for v in vertices])
    
    #######
    # build a trivial solution
    # every node has its own color

    # prepare the solution in the specified output format
    output_data = str(num_colors) + ' ' + str(0) + '\n'
    output_data += ' '.join(map(str, solution))

    return output_data, vertex_colors, color_frequency


In [ ]:
data_folder = 'C:/D/coursera/discrete_opt/coloring/data'
filename = os.path.join(data_folder,'gc_1000_7')
with open(filename, 'r') as input_data_file:
    input_data = input_data_file.read()
    
output, vertex_colors, color_frequency = solve_it(input_data)
print('\n\nVertex colors\n', vertex_colors)
print('\n\nColors frequence\n', color_frequency)
print('\n\n Output\n', output)


In graph_coloring, Start set new color 1 to index 579 with degree 743


In check_all_node, check index 579
In graph_coloring_probe, pindx None, cindex 579
Vertex 579 already have color
In graph_coloring_probe, index 579: node_coloring return True with color None
In graph_coloring_probe, check child of 579

In graph_coloring_probe, check child 0 of parent 579
More than 1 color to use
In graph_coloring_probe, index 0: node_coloring return False with color None
In graph_coloring_probe, no color to set

In graph_coloring_probe, check child 1 of parent 579
More than 1 color to use
In graph_coloring_probe, index 1: node_coloring return False with color None
In graph_coloring_probe, no color to set

In graph_coloring_probe, check child 2 of parent 579
More than 1 color to use
In graph_coloring_probe, index 2: node_coloring return False with color None
In graph_coloring_probe, no color to set

In graph_coloring_probe, check child 3 of parent 579
More than 1 color to use
In graph_coloring_prob

In [356]:
data_folder = 'C:/D/coursera/discrete_opt/coloring/data'
filename = os.path.join(data_folder,'gc_11_16')
with open(filename, 'r') as input_data_file:
    input_data = input_data_file.read()
    
output, vertex_colors, color_frequency = solve_it(input_data)
print('\n\nVertex colors\n', vertex_colors)
print('\n\nColors frequence\n', color_frequency)
print('\n\n Output\n', output)


In graph_coloring, Start set new color 1 to index 1 with degree 6
In check_all_node, index 0, child colors [1, None]
In check_all_node, index 1, child colors [None, None, None, None, None, None]
In check_all_node, index 2, child colors [1, None, None, None, None]
In check_all_node, index 3, child colors [1, None, None]
In check_all_node, index 4, child colors [None, None, None]
In check_all_node, index 5, child colors [None, None, None]
In check_all_node, index 6, child colors [None, None]
In check_all_node, index 7, child colors [None, None, None]
In check_all_node, index 8, child colors [None]
In check_all_node, index 9, child colors [None]
In check_all_node, index 10, child colors [1]
In check_all_node, index 11, child colors [1]
In check_all_node, index 12, child colors [1]

In check_all_node, vertex info  [(-6, 1), (-3, 3), (-5, 2), (-3, 7), (-3, 4), (-3, 5), (-2, 6), (-2, 0), (-1, 8), (-1, 9), (-1, 10), (-1, 11), (-1, 12)]


In check_all_node, check index 1
In graph_coloring_pro

In [ ]:
def select_value_forward_checking(i, domains, vertices):
    
    ldomains = copy.deepcopy(domains)
    print('\n\nIn select_value_forward_checking, Copied domains ', ldomains)
    domain = ldomains[i]
    print('In select_value_forward_checking, Vertex {}, Domain {}'.format(i, domain))
    while domain:
        a_i = select_value(domain)
        print('In select_value_forward_checking, Selected value ', a_i)
        invalid_assignment = False
        print('In select_value_forward_checking, vertices[i].child_indices ', vertices[i].child_indices)
        for k in vertices[i].child_indices: 
            print('-----In select_value_forward_checking, Domain {} of cidx {} in {}'.format(ldomains[k], k, vertices[i].child_indices))
            for a_k in ldomains[k]:
                print('\n------In select_value_forward_checking, value {} in domain {} of vertex {}'.format(a_k, ldomains[k], k))
                print('\n------directed_arc_consistency {}'.format(directed_arc_consistency(vertices, i, a_i, k, a_k)))
                if not directed_arc_consistency(vertices, i, a_i, k, a_k):
                    del ldomains[k][ldomains[k].index(a_k)]
                    print('------In select_value_forward_checking, remove value {} in domain {}'.format(a_k, ldomains[k]))
            if len(ldomains[k]) == 0:
                invalid_assignment = True
                print('In select_value_forward_checking, invalid assignment')
                break
        if invalid_assignment:
            for k in vertices[i].child_indices: 
                print('In select_value_forward_checking, for vertex {}, reverse domains {} to previous domains{}'.format(k, ldomains[k] ,copy.deepcopy(domains[k]) ))
                ldomains[k] = copy.deepcopy(domains[k])
        else:
            print('In select_value_forward_checking, returned domain {} with color {}'.format(ldomains, a_i))
            ldomains[i] = [a_i]
            return ldomains, a_i
        
        print('In select_value_forward_checking, return old domains ', ldomains)
        
    return ldomains, None